In [3]:
import pandas as pd
data = pd.read_csv("classification.csv")

In [4]:
data.head()

Age  EstimatedSalary  Purchased
0   19            19000          0
1   35            20000          0
2   26            43000          0
3   27            57000          0
4   19            76000          0

In [5]:
def group_list(lst):
     
    res =  []
    vis=[]
    for el in lst:
        if el not in vis:
            vis.append(el)
            res.append([el, lst.count(el)])
    return res

In [6]:

def gini_index(column,purchased):
    #c3 = df[[column,'Purchased']]
    
    column = list(column)
    #column.sort()
    n = len(column)
    c3 = []
    c3.extend([list(a) for a in zip(column, purchased)])
    print(c3)
    c3 = group_list(c3)
    c3.sort(key = lambda x:x[0][0])
    print(c3)

    if c3:
        gini = 0
        count = [0,0]
        temp = c3[0][0][0]

        #for i in column:
            #data = c3[c3[column == i]]

        for j in c3:
            if j[0][0] == temp:
                count[j[0][1]] += j[1]
            else:
                tot = count[0] + count[1]
                gini += (tot/n)*(1 - ((count[0]/tot)**2 + (count[1]/tot)**2))
                count = [0,0]
                temp = j[0][0]

                count[j[0][1]] += j[1]

        return gini
    return 1000


In [7]:
gini_index(data['EstimatedSalary'],data['Purchased'])

[[19000, 0], [20000, 0], [43000, 0], [57000, 0], [76000, 0], [58000, 0], [84000, 0], [150000, 1], [33000, 0], [65000, 0], [80000, 0], [52000, 0], [86000, 0], [18000, 0], [82000, 0], [80000, 0], [25000, 1], [26000, 1], [28000, 1], [29000, 1], [22000, 1], [49000, 1], [41000, 1], [22000, 1], [23000, 1], [20000, 1], [28000, 1], [30000, 1], [43000, 0], [18000, 0], [74000, 0], [137000, 1], [16000, 0], [44000, 0], [90000, 0], [27000, 0], [28000, 0], [49000, 0], [72000, 0], [31000, 0], [17000, 0], [51000, 0], [108000, 0], [15000, 0], [84000, 0], [20000, 0], [79000, 0], [54000, 0], [135000, 1], [89000, 0], [32000, 0], [44000, 0], [83000, 0], [23000, 0], [58000, 0], [55000, 0], [48000, 0], [79000, 0], [18000, 0], [117000, 0], [20000, 0], [87000, 0], [66000, 0], [120000, 1], [83000, 0], [58000, 0], [19000, 0], [82000, 0], [63000, 0], [68000, 0], [80000, 0], [27000, 0], [23000, 0], [113000, 0], [18000, 0], [112000, 1], [52000, 0], [27000, 0], [87000, 0], [17000, 0], [80000, 0], [42000, 0], [49000,

0.22002958152958152

In [8]:
y = data['Purchased'].values
X = data.drop(columns=['Purchased'],axis=1)

from sklearn.model_selection import train_test_split
x_train,x_test,y_train,y_test = train_test_split(X,y,test_size=0.3,random_state=100)


In [11]:
import numpy as np

class TreeNode:
    def __init__(self, data=None, level=None, threshold=None, target_class=None, left=None, right=None):
        self.data = data  
        self.level = level
        self.threshold = threshold 
        self.target_class = target_class  
        self.left = left      
        self.right = right 

    def predict(self,x):
        
        #print(x[self.data],self.threshold,self.target_class)
        
        if self.target_class is not None:
            return self.target_class
        
        if self.data is not None:
            
            if x[self.data] < self.threshold:
                
                #print(x[self.data],self.threshold,'left',self.target_class)
                return self.left.predict(x)
            else:
                
                #print(x[self.data],self.threshold,'right',self.target_class)
                return self.right.predict(x)
            
def print2DUtil(root, space):
 
    # Base case
    if (root == None):
        return
 
    # Increase distance between levels
    space += COUNT[0]
 
    # Process right child first
    print2DUtil(root.right, space)
 
    # Print current node after space
    # count
    print()
    for i in range(COUNT[0], space):
        print(end=" ")
    print(root.target_class,root.level)
 
    # Process left child
    print2DUtil(root.left, space)
 
 
def print2D(root):
 
    # space=[0]
    # Pass initial space count as 0
    print2DUtil(root, 0)
 
            
def decision_tree(x,y,max_depth=float('inf'),lvl=0):
    
    x.reset_index(drop=True, inplace=True)
    
    if len(set(y)) == 1 or max_depth == 0 or len(y) < 10:
        y = list(y)
        return TreeNode(level=lvl, target_class= max(y, key=lambda x:y.count(x)))

    best_feature, best_threshold = find_best_split(x, y)

    if best_feature is None:
        y = list(y)
        return TreeNode(level=lvl, target_class=max(y, key=lambda x:y.count(x)))
    
    
    left_indices = x.iloc[:,best_feature:best_feature+1] <= best_threshold
    mask = left_indices.iloc[:,0].isin([True])
    left_indices = left_indices[mask]
    left_indices = list(left_indices.index)
    
        
    right_indices = x.iloc[:,best_feature:best_feature+1] > best_threshold
    mask = right_indices.iloc[:,0].isin([True])
    right_indices = right_indices[mask]
    right_indices = list(right_indices.index)
    
    left_child = decision_tree(x.iloc[left_indices,:], y[left_indices],max_depth-1,lvl+1)
    right_child = decision_tree(x.iloc[right_indices,:], y[right_indices],max_depth-1,lvl+1)
    #print(best_feature,best_threshold)
    return TreeNode(data=best_feature, level=lvl, threshold=best_threshold, left=left_child, right=right_child)

def find_best_split(X, y):
    
    num_samples, num_features = X.shape
    best_gini = float('inf')
    best_feature = None
    best_threshold = None

    for feature in range(1,num_features+1):
        
        feature_values = X.iloc[:,feature-1:feature]
        unique_values = np.unique(feature_values)
        
        for threshold in unique_values:
            
            left_indices = feature_values <= threshold
            mask = left_indices.iloc[:,0].isin([True])
            left_indices = left_indices[mask]
            left_indices = list(left_indices.index)
        
            
            right_indices = feature_values > threshold
            mask = right_indices.iloc[:,0].isin([True])
            right_indices = right_indices[mask]
            right_indices = list(right_indices.index)
            
            gini = gini_index(X.iloc[left_indices,feature-1],y[left_indices]) + gini_index(X.iloc[right_indices,feature-1],y[right_indices])
            if gini < best_gini:
                best_gini = gini
                best_feature = feature
                best_threshold = threshold

    return best_feature-1, best_threshold

COUNT = [10]
tree = decision_tree(x_train,y_train,25)
#print2D(tree)



[[18, 0], [18, 0], [18, 0], [18, 0], [18, 0]]
[[[18, 0], 5]]
[[38, 0], [23, 0], [34, 0], [27, 0], [42, 1], [32, 1], [49, 1], [36, 0], [32, 0], [26, 0], [35, 1], [57, 1], [37, 0], [30, 0], [49, 1], [35, 0], [35, 0], [37, 0], [27, 0], [50, 0], [48, 1], [26, 0], [46, 0], [26, 0], [46, 0], [36, 0], [24, 0], [37, 0], [53, 1], [49, 1], [41, 0], [33, 0], [49, 1], [59, 1], [19, 0], [30, 0], [42, 0], [25, 0], [35, 0], [53, 1], [27, 0], [56, 1], [21, 0], [30, 1], [43, 1], [36, 1], [35, 0], [45, 1], [39, 0], [25, 0], [24, 0], [45, 1], [38, 0], [42, 0], [40, 0], [35, 0], [31, 1], [32, 1], [33, 0], [29, 0], [41, 0], [40, 0], [42, 1], [41, 0], [31, 0], [58, 1], [19, 0], [38, 0], [41, 0], [37, 0], [37, 0], [40, 0], [25, 0], [58, 1], [60, 1], [23, 0], [39, 1], [48, 1], [48, 1], [53, 1], [23, 0], [40, 0], [28, 0], [52, 1], [38, 0], [30, 0], [28, 0], [49, 0], [60, 1], [35, 0], [51, 0], [40, 0], [47, 1], [38, 0], [41, 1], [35, 0], [59, 1], [53, 1], [35, 0], [41, 0], [31, 0], [28, 0], [42, 0], [24, 0], [4

[[20000, 0], [54000, 0], [36000, 1], [75000, 0], [81000, 0], [57000, 0], [28000, 1], [22000, 0], [27000, 0], [75000, 0], [31000, 0], [44000, 0], [74000, 1], [80000, 0], [22000, 0], [15000, 0], [74000, 0], [60000, 0], [58000, 0], [77000, 0], [34000, 1], [30000, 0], [51000, 0], [28000, 1], [21000, 0], [17000, 0], [54000, 0], [59000, 0], [82000, 1], [17000, 0], [16000, 0], [53000, 0], [73000, 0], [27000, 0], [45000, 1], [55000, 0], [65000, 0], [57000, 0], [61000, 0], [69000, 0], [83000, 0], [71000, 0], [47000, 0], [52000, 0], [18000, 0], [47000, 1], [25000, 0], [50000, 0], [72000, 0], [33000, 0], [71000, 0], [60000, 0], [22000, 0], [23000, 1], [34000, 1], [28000, 0], [72000, 1], [66000, 0], [57000, 0], [37000, 0], [61000, 0], [49000, 0], [32000, 0], [65000, 0], [83000, 1], [75000, 0], [44000, 0], [61000, 0], [29000, 1], [50000, 0], [60000, 0], [34000, 0], [70000, 0], [55000, 0], [41000, 1], [59000, 0], [52000, 0], [79000, 0], [33000, 1], [20000, 1], [52000, 0], [42000, 0], [80000, 0], [60

[[20000, 0], [22000, 0], [22000, 0], [15000, 0], [21000, 0], [17000, 0], [17000, 0], [16000, 0], [18000, 0], [25000, 0], [22000, 0], [23000, 1], [20000, 1], [18000, 0], [23000, 1], [23000, 1], [25000, 0], [15000, 0], [25000, 1], [16000, 0], [19000, 0], [23000, 1], [26000, 1], [18000, 0], [23000, 0], [26000, 1], [21000, 1], [20000, 1], [15000, 0], [18000, 0], [19000, 0], [23000, 0], [17000, 0]]
[[[15000, 0], 3], [[16000, 0], 2], [[17000, 0], 3], [[18000, 0], 4], [[19000, 0], 2], [[20000, 0], 1], [[20000, 1], 2], [[21000, 0], 1], [[21000, 1], 1], [[22000, 0], 3], [[23000, 1], 4], [[23000, 0], 2], [[25000, 0], 2], [[25000, 1], 1], [[26000, 1], 2]]
[[112000, 0], [115000, 0], [54000, 0], [108000, 1], [100000, 1], [36000, 1], [75000, 0], [117000, 0], [81000, 0], [97000, 1], [122000, 1], [57000, 0], [87000, 0], [28000, 1], [27000, 0], [75000, 0], [31000, 0], [44000, 0], [74000, 1], [80000, 0], [74000, 0], [60000, 0], [58000, 0], [77000, 0], [34000, 1], [89000, 1], [30000, 0], [51000, 0], [280

[[19, 0], [21, 0], [19, 0], [18, 0], [20, 0], [22, 0], [20, 0], [20, 0], [18, 0], [18, 0], [21, 0], [19, 0], [22, 0], [20, 0], [21, 0], [19, 0], [19, 0], [18, 0], [22, 0], [18, 0]]
[[[18, 0], 5], [[19, 0], 5], [[20, 0], 4], [[21, 0], 3], [[22, 0], 3]]
[[38, 0], [23, 0], [34, 0], [27, 0], [42, 1], [32, 1], [49, 1], [36, 0], [32, 0], [26, 0], [35, 1], [57, 1], [37, 0], [30, 0], [49, 1], [35, 0], [35, 0], [37, 0], [27, 0], [50, 0], [48, 1], [26, 0], [46, 0], [26, 0], [46, 0], [36, 0], [24, 0], [37, 0], [53, 1], [49, 1], [41, 0], [33, 0], [49, 1], [59, 1], [30, 0], [42, 0], [25, 0], [35, 0], [53, 1], [27, 0], [56, 1], [30, 1], [43, 1], [36, 1], [35, 0], [45, 1], [39, 0], [25, 0], [24, 0], [45, 1], [38, 0], [42, 0], [40, 0], [35, 0], [31, 1], [32, 1], [33, 0], [29, 0], [41, 0], [40, 0], [42, 1], [41, 0], [31, 0], [58, 1], [38, 0], [41, 0], [37, 0], [37, 0], [40, 0], [25, 0], [58, 1], [60, 1], [23, 0], [39, 1], [48, 1], [48, 1], [53, 1], [23, 0], [40, 0], [28, 0], [52, 1], [38, 0], [30, 0], 

[[20000, 0], [54000, 0], [36000, 1], [75000, 0], [81000, 0], [57000, 0], [87000, 0], [28000, 1], [22000, 0], [27000, 0], [75000, 0], [31000, 0], [44000, 0], [74000, 1], [80000, 0], [22000, 0], [15000, 0], [74000, 0], [60000, 0], [58000, 0], [77000, 0], [34000, 1], [89000, 1], [30000, 0], [51000, 0], [28000, 1], [21000, 0], [17000, 0], [54000, 0], [90000, 0], [59000, 0], [82000, 1], [17000, 0], [16000, 0], [53000, 0], [73000, 0], [87000, 0], [27000, 0], [45000, 1], [55000, 0], [65000, 0], [57000, 0], [61000, 0], [69000, 0], [83000, 0], [71000, 0], [47000, 0], [90000, 1], [52000, 0], [18000, 0], [47000, 1], [25000, 0], [50000, 0], [72000, 0], [33000, 0], [71000, 0], [60000, 0], [22000, 0], [23000, 1], [34000, 1], [28000, 0], [72000, 1], [66000, 0], [57000, 0], [37000, 0], [90000, 1], [61000, 0], [49000, 0], [32000, 0], [65000, 0], [83000, 1], [88000, 0], [75000, 0], [44000, 0], [61000, 0], [87000, 1], [29000, 1], [50000, 0], [60000, 0], [34000, 0], [85000, 0], [70000, 0], [55000, 0], [41

...

[[20000, 0], [15000, 0], [21000, 0], [17000, 0], [17000, 0], [16000, 0], [18000, 0], [20000, 1], [18000, 0], [15000, 0], [16000, 0], [19000, 0], [18000, 0], [21000, 1], [20000, 1], [15000, 0], [18000, 0], [19000, 0], [17000, 0]]
[[[15000, 0], 3], [[16000, 0], 2], [[17000, 0], 3], [[18000, 0], 4], [[19000, 0], 2], [[20000, 0], 1], [[20000, 1], 2], [[21000, 0], 1], [[21000, 1], 1]]
[[112000, 0], [115000, 0], [54000, 0], [108000, 1], [100000, 1], [36000, 1], [75000, 0], [117000, 0], [81000, 0], [97000, 1], [122000, 1], [57000, 0], [87000, 0], [28000, 1], [22000, 0], [27000, 0], [75000, 0], [31000, 0], [44000, 0], [74000, 1], [80000, 0], [22000, 0], [74000, 0], [60000, 0], [58000, 0], [77000, 0], [34000, 1], [89000, 1], [30000, 0], [51000, 0], [28000, 1], [54000, 0], [90000, 0], [59000, 0], [82000, 1], [129000, 1], [118000, 1], [53000, 0], [131000, 1], [73000, 0], [87000, 0], [27000, 0], [45000, 1], [55000, 0], [65000, 0], [57000, 0], [61000, 0], [118000, 1], [69000, 0], [83000, 0], [71000

[[38, 0], [23, 0], [34, 0], [27, 0], [42, 1], [32, 1], [49, 1], [36, 0], [32, 0], [26, 0], [35, 1], [37, 0], [30, 0], [49, 1], [35, 0], [35, 0], [37, 0], [27, 0], [50, 0], [48, 1], [26, 0], [46, 0], [26, 0], [46, 0], [36, 0], [24, 0], [37, 0], [49, 1], [41, 0], [33, 0], [49, 1], [19, 0], [30, 0], [42, 0], [25, 0], [35, 0], [27, 0], [21, 0], [43, 1], [36, 1], [35, 0], [39, 0], [25, 0], [24, 0], [45, 1], [38, 0], [42, 0], [40, 0], [35, 0], [31, 1], [33, 0], [29, 0], [41, 0], [40, 0], [42, 1], [41, 0], [31, 0], [19, 0], [38, 0], [41, 0], [37, 0], [37, 0], [40, 0], [25, 0], [23, 0], [39, 1], [48, 1], [23, 0], [40, 0], [28, 0], [52, 1], [38, 0], [30, 0], [28, 0], [49, 0], [35, 0], [40, 0], [18, 0], [38, 0], [41, 1], [35, 0], [35, 0], [41, 0], [31, 0], [28, 0], [42, 0], [24, 0], [48, 1], [43, 1], [28, 0], [26, 0], [45, 0], [26, 0], [28, 0], [47, 1], [36, 0], [39, 0], [37, 0], [20, 0], [38, 0], [46, 0], [35, 0], [35, 0], [32, 0], [35, 0], [35, 1], [46, 0], [24, 0], [42, 0], [31, 0], [37, 0], 

[[38, 0], [23, 0], [34, 0], [27, 0], [42, 1], [32, 1], [36, 0], [32, 0], [26, 0], [35, 1], [37, 0], [30, 0], [35, 0], [35, 0], [37, 0], [27, 0], [26, 0], [26, 0], [36, 0], [24, 0], [37, 0], [41, 0], [33, 0], [19, 0], [30, 0], [42, 0], [25, 0], [35, 0], [27, 0], [21, 0], [36, 1], [35, 0], [39, 0], [25, 0], [24, 0], [38, 0], [42, 0], [40, 0], [35, 0], [31, 1], [33, 0], [29, 0], [41, 0], [40, 0], [42, 1], [41, 0], [31, 0], [19, 0], [38, 0], [41, 0], [37, 0], [37, 0], [40, 0], [25, 0], [23, 0], [23, 0], [40, 0], [28, 0], [38, 0], [30, 0], [28, 0], [35, 0], [40, 0], [18, 0], [38, 0], [41, 1], [35, 0], [35, 0], [41, 0], [31, 0], [28, 0], [42, 0], [24, 0], [43, 1], [28, 0], [26, 0], [26, 0], [28, 0], [36, 0], [39, 0], [37, 0], [20, 0], [38, 0], [35, 0], [35, 0], [32, 0], [35, 0], [35, 1], [24, 0], [42, 0], [31, 0], [37, 0], [41, 0], [29, 0], [22, 0], [40, 0], [27, 0], [34, 0], [32, 1], [40, 1], [33, 0], [28, 0], [28, 0], [26, 0], [27, 1], [35, 0], [28, 0], [38, 0], [41, 0], [23, 0], [38, 0], 

[[23, 0], [26, 0], [26, 0], [26, 0], [24, 0], [19, 0], [25, 0], [21, 0], [25, 0], [24, 0], [19, 0], [25, 0], [23, 0], [23, 0], [18, 0], [24, 0], [26, 0], [26, 0], [20, 0], [24, 0], [22, 0], [26, 0], [23, 0], [20, 0], [20, 0], [18, 0], [18, 0], [21, 0], [26, 0], [26, 0], [25, 0], [19, 0], [22, 0], [26, 0], [20, 0], [21, 0], [26, 0], [19, 0], [23, 0], [19, 0], [18, 0], [24, 0], [22, 0], [18, 0], [24, 0], [26, 0], [25, 0]]
[[[18, 0], 5], [[19, 0], 5], [[20, 0], 4], [[21, 0], 3], [[22, 0], 3], [[23, 0], 5], [[24, 0], 6], [[25, 0], 5], [[26, 0], 11]]
[[38, 0], [34, 0], [27, 0], [42, 1], [32, 1], [49, 1], [36, 0], [32, 0], [35, 1], [37, 0], [30, 0], [49, 1], [35, 0], [35, 0], [37, 0], [27, 0], [50, 0], [48, 1], [46, 0], [46, 0], [36, 0], [37, 0], [53, 1], [49, 1], [41, 0], [33, 0], [49, 1], [30, 0], [42, 0], [35, 0], [53, 1], [27, 0], [35, 0], [39, 0], [45, 1], [38, 0], [42, 0], [40, 0], [35, 0], [33, 0], [29, 0], [41, 0], [40, 0], [42, 1], [41, 0], [31, 0], [38, 0], [41, 0], [37, 0], [37, 0

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [12]:
count = 0
tot = 0
for i in range (len(x_test)):
    test = list(x_test.iloc[i,:])
    pred = tree.predict(test)
    #print(test,pred,y_test[i])
    if pred == y_test[i]:
        count=count+1
    tot = tot+1
print(count/tot*100)

88.33333333333333
